1- CArregar os dados do dataset para o datafram(ggeolocation_df)

In [1]:
import pyspark
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, length, udf
from pyspark.sql.types import StructType, StringType, DoubleType
import time

spark = SparkSession.builder\
    .master("local") \
    .appName("update_geolocalization")\
    .enableHiveSupport()\
    .getOrCreate()

In [2]:
schema = StructType() \
      .add("geolocation_zip_code_prefix",StringType(),True) \
      .add("geolocation_lat",DoubleType(),True) \
      .add("geolocation_lng",DoubleType(),True) \
      .add("geolocation_city",StringType(),True) \
      .add("geolocation_state",StringType(),True) 


geolocation_df = spark.read.option("header",True) \
                       .option("delimiter",",") \
                       .schema(schema) \
                       .csv("hdfs://namenode:8020/datalake/olist/raw/csv/olist_geolocation_dataset.csv")

print(geolocation_df.count())
print(geolocation_df.printSchema())
geolocation_df.cache()


1000163
root
 |-- geolocation_zip_code_prefix: string (nullable = true)
 |-- geolocation_lat: double (nullable = true)
 |-- geolocation_lng: double (nullable = true)
 |-- geolocation_city: string (nullable = true)
 |-- geolocation_state: string (nullable = true)

None


DataFrame[geolocation_zip_code_prefix: string, geolocation_lat: double, geolocation_lng: double, geolocation_city: string, geolocation_state: string]

In [3]:
geoclocation_cep_distinct_df = geolocation_df.select("geolocation_zip_code_prefix").distinct()
geoclocation_cep_distinct_df.cache()

print(geoclocation_cep_distinct_df.count())

19015


In [4]:
def formatCep(cep):
    cep_formatado = cep
    
    cep_formatado.zfill(5)
    
    if(len(cep_formatado) == 5):
        cep_formatado = cep_formatado + "-000"
        
    return cep_formatado

formatCepUDF = udf(lambda z:formatCep(z),StringType())

In [7]:
geolocation_formattedCep_distinct_df = geoclocation_cep_distinct_df.select(formatCepUDF(col("geolocation_zip_code_prefix")).alias("geolocation_zip_code_prefix"))\
                                                                .sort("geolocation_zip_code_prefix")

geolocation_formattedCep_distinct_df.cache()

DataFrame[geolocation_zip_code_prefix: string]

In [8]:
geolocation_formattedCep_distinct_df.show()
geolocation_formattedCep_distinct_df.count()

+---------------------------+
|geolocation_zip_code_prefix|
+---------------------------+
|                  01001-000|
|                  01002-000|
|                  01003-000|
|                  01004-000|
|                  01005-000|
|                  01006-000|
|                  01007-000|
|                  01008-000|
|                  01009-000|
|                  01010-000|
|                  01011-000|
|                  01012-000|
|                  01013-000|
|                  01014-000|
|                  01015-000|
|                  01016-000|
|                  01017-000|
|                  01018-000|
|                  01019-000|
|                  01020-000|
+---------------------------+
only showing top 20 rows



19015

1- Instalando a API Correios

In [6]:
! pip install pycep-correios

Consultando a API pycep_correios. Este código foi construido com base na documentação do pycep.

In [7]:
import time
from pycep_correios import get_address_from_cep, WebService, exceptions


def addAddressByCorreios(row):    
    rowDict = row.asDict()
    cep = rowDict.get("geolocation_zip_code_prefix")
    print(cep)

    try:
        address_json = get_address_from_cep(str(cep), webservice=WebService.VIACEP)
        rowDict["geolocation_city"] = address_json["cidade"]
        rowDict["geolocation_state"] = address_json["uf"]
        rowDict["geolocation_street"] = address_json["logradouro"]
        
    except exceptions.CEPNotFound as ecnf:
        rowDict["geolocation_city"] = ''
        rowDict["geolocation_state"] = ''
        rowDict["geolocation_street"] = ''

    except exceptions.ConnectionError as errc:
        rowDict["geolocation_city"] = '-1'
        rowDict["geolocation_state"] = '-1'
        rowDict["geolocation_street"] = '-1'
        
    except exceptions.InvalidCEP as icnf:
        rowDict["geolocation_city"] = '-2'
        rowDict["geolocation_state"] = '-2'
        rowDict["geolocation_street"] = '-2'
    
    print(rowDict)
    time.sleep(4)
    return rowDict

In [8]:
geolocation_formattedCep_rows = geolocation_formattedCep_distinct_df.collect()

In [36]:
print(geolocation_formattedCep_rows)

[Row(geolocation_zip_code_prefix='01001-000'), Row(geolocation_zip_code_prefix='01002-000'), Row(geolocation_zip_code_prefix='01003-000'), Row(geolocation_zip_code_prefix='01004-000'), Row(geolocation_zip_code_prefix='01005-000'), Row(geolocation_zip_code_prefix='01006-000'), Row(geolocation_zip_code_prefix='01007-000'), Row(geolocation_zip_code_prefix='01008-000'), Row(geolocation_zip_code_prefix='01009-000'), Row(geolocation_zip_code_prefix='01010-000'), Row(geolocation_zip_code_prefix='01011-000'), Row(geolocation_zip_code_prefix='01012-000'), Row(geolocation_zip_code_prefix='01013-000'), Row(geolocation_zip_code_prefix='01014-000'), Row(geolocation_zip_code_prefix='01015-000'), Row(geolocation_zip_code_prefix='01016-000'), Row(geolocation_zip_code_prefix='01017-000'), Row(geolocation_zip_code_prefix='01018-000'), Row(geolocation_zip_code_prefix='01019-000'), Row(geolocation_zip_code_prefix='01020-000'), Row(geolocation_zip_code_prefix='01021-000'), Row(geolocation_zip_code_prefix='

Faz a consuta do CEP quue estão no dataset 

In [9]:
import pandas as pd

geolocation_formattedCep_address = [
    addAddressByCorreios(row) for row in geolocation_formattedCep_rows]


01001-000
{'geolocation_zip_code_prefix': '01001-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Praça da Sé'}
01002-000
{'geolocation_zip_code_prefix': '01002-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua Direita'}
01003-000
{'geolocation_zip_code_prefix': '01003-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua José Bonifácio'}
01004-000
{'geolocation_zip_code_prefix': '01004-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua Barão de Paranapiacaba'}
01005-000
{'geolocation_zip_code_prefix': '01005-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua Benjamim Constant'}
01006-000
{'geolocation_zip_code_prefix': '01006-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua Senador Feijó'}
01007-000
{'geolocation_zip_code_prefix': '01007-0

01103-000
{'geolocation_zip_code_prefix': '01103-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua Vinte e Cinco de Janeiro'}
01104-000
{'geolocation_zip_code_prefix': '01104-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua São Caetano'}
01105-000
{'geolocation_zip_code_prefix': '01105-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua João Teodoro'}
01106-000
{'geolocation_zip_code_prefix': '01106-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua Jorge Miranda'}
01107-000
{'geolocation_zip_code_prefix': '01107-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Avenida do Estado'}
01108-000
{'geolocation_zip_code_prefix': '01108-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Avenida do Estado'}
01109-000
{'geolocation_zip_code_prefix': '0

01214-000
{'geolocation_zip_code_prefix': '01214-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Avenida Duque de Caxias'}
01215-000
{'geolocation_zip_code_prefix': '01215-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Alameda Glete'}
01216-000
{'geolocation_zip_code_prefix': '01216-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Alameda Nothmann'}
01217-000
{'geolocation_zip_code_prefix': '01217-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Alameda Dino Bueno'}
01218-000
{'geolocation_zip_code_prefix': '01218-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Alameda Cleveland'}
01219-000
{'geolocation_zip_code_prefix': '01219-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua do Arouche'}
01220-000
{'geolocation_zip_code_prefix': '01220-000'

01306-000
{'geolocation_zip_code_prefix': '01306-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua Avanhandava'}
01307-000
{'geolocation_zip_code_prefix': '01307-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua Frei Caneca'}
01308-000
{'geolocation_zip_code_prefix': '01308-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua Barata Ribeiro'}
01309-000
{'geolocation_zip_code_prefix': '01309-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua Luís Coelho'}
01310-000
{'geolocation_zip_code_prefix': '01310-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Avenida Paulista'}
01311-000
{'geolocation_zip_code_prefix': '01311-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Avenida Paulista'}
01312-000
{'geolocation_zip_code_prefix': '01312-000', 'geo

01425-000
{'geolocation_zip_code_prefix': '01425-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua Guarará'}
01426-000
{'geolocation_zip_code_prefix': '01426-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua Oscar Freire'}
01427-000
{'geolocation_zip_code_prefix': '01427-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua Estados Unidos'}
01428-000
{'geolocation_zip_code_prefix': '01428-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua Honduras'}
01429-000
{'geolocation_zip_code_prefix': '01429-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Rua Doutor João Pinheiro'}
01430-000
{'geolocation_zip_code_prefix': '01430-000', 'geolocation_city': 'São Paulo', 'geolocation_state': 'SP', 'geolocation_street': 'Avenida Brasil'}
01431-000
{'geolocation_zip_code_prefix': '01431-000', 'geo

...

98130-000
{'geolocation_zip_code_prefix': '98130-000', 'geolocation_city': 'Júlio de Castilhos', 'geolocation_state': 'RS', 'geolocation_street': ''}
98140-000
{'geolocation_zip_code_prefix': '98140-000', 'geolocation_city': 'Quevedos', 'geolocation_state': 'RS', 'geolocation_street': ''}
98150-000
{'geolocation_zip_code_prefix': '98150-000', 'geolocation_city': 'Pinhal Grande', 'geolocation_state': 'RS', 'geolocation_street': ''}
98160-000
{'geolocation_zip_code_prefix': '98160-000', 'geolocation_city': 'Ivorá', 'geolocation_state': 'RS', 'geolocation_street': ''}
98170-000
{'geolocation_zip_code_prefix': '98170-000', 'geolocation_city': 'Tupanciretã', 'geolocation_state': 'RS', 'geolocation_street': ''}
98175-000
{'geolocation_zip_code_prefix': '98175-000', 'geolocation_city': 'Jari', 'geolocation_state': 'RS', 'geolocation_street': ''}
98180-000
{'geolocation_zip_code_prefix': '98180-000', 'geolocation_city': 'Jóia', 'geolocation_state': 'RS', 'geolocation_street': ''}
98200-000
{'g

98675-000
{'geolocation_zip_code_prefix': '98675-000', 'geolocation_city': 'Sede Nova', 'geolocation_state': 'RS', 'geolocation_street': ''}
98680-000
{'geolocation_zip_code_prefix': '98680-000', 'geolocation_city': 'Tiradentes do Sul', 'geolocation_state': 'RS', 'geolocation_street': ''}
98690-000
{'geolocation_zip_code_prefix': '98690-000', 'geolocation_city': 'São Martinho', 'geolocation_state': 'RS', 'geolocation_street': ''}
98700-000
{'geolocation_zip_code_prefix': '98700-000', 'geolocation_city': 'Ijuí', 'geolocation_state': 'RS', 'geolocation_street': ''}
98733-000
{'geolocation_zip_code_prefix': '98733-000', 'geolocation_city': 'Bozano', 'geolocation_state': 'RS', 'geolocation_street': ''}
98735-000
{'geolocation_zip_code_prefix': '98735-000', 'geolocation_city': 'Coronel Barros', 'geolocation_state': 'RS', 'geolocation_street': ''}
98740-000
{'geolocation_zip_code_prefix': '98740-000', 'geolocation_city': 'Augusto Pestana', 'geolocation_state': 'RS', 'geolocation_street': ''}

99020-000
{'geolocation_zip_code_prefix': '99020-000', 'geolocation_city': 'Passo Fundo', 'geolocation_state': 'RS', 'geolocation_street': 'Rua Nascimento Vargas'}
99022-000
{'geolocation_zip_code_prefix': '99022-000', 'geolocation_city': 'Passo Fundo', 'geolocation_state': 'RS', 'geolocation_street': 'Rua Lalau Miranda'}
99025-000
{'geolocation_zip_code_prefix': '99025-000', 'geolocation_city': 'Passo Fundo', 'geolocation_state': 'RS', 'geolocation_street': 'Avenida Brasil Oeste'}
99030-000
{'geolocation_zip_code_prefix': '99030-000', 'geolocation_city': '', 'geolocation_state': '', 'geolocation_street': ''}
99032-000
{'geolocation_zip_code_prefix': '99032-000', 'geolocation_city': 'Passo Fundo', 'geolocation_state': 'RS', 'geolocation_street': 'Avenida Luiz Langaro'}
99034-000
{'geolocation_zip_code_prefix': '99034-000', 'geolocation_city': 'Passo Fundo', 'geolocation_state': 'RS', 'geolocation_street': 'Rua Nicolau José Ribeiro'}
99036-000
{'geolocation_zip_code_prefix': '99036-000'

99457-000
{'geolocation_zip_code_prefix': '99457-000', 'geolocation_city': 'Jacuizinho', 'geolocation_state': 'RS', 'geolocation_street': ''}
99460-000
{'geolocation_zip_code_prefix': '99460-000', 'geolocation_city': 'Colorado', 'geolocation_state': 'RS', 'geolocation_street': ''}
99470-000
{'geolocation_zip_code_prefix': '99470-000', 'geolocation_city': 'Não-Me-Toque', 'geolocation_state': 'RS', 'geolocation_street': ''}
99490-000
{'geolocation_zip_code_prefix': '99490-000', 'geolocation_city': 'Tapera', 'geolocation_state': 'RS', 'geolocation_street': ''}
99495-000
{'geolocation_zip_code_prefix': '99495-000', 'geolocation_city': 'Lagoa dos Três Cantos', 'geolocation_state': 'RS', 'geolocation_street': ''}
99500-000
{'geolocation_zip_code_prefix': '99500-000', 'geolocation_city': 'Carazinho', 'geolocation_state': 'RS', 'geolocation_street': ''}
99523-000
{'geolocation_zip_code_prefix': '99523-000', 'geolocation_city': 'Almirante Tamandaré do Sul', 'geolocation_state': 'RS', 'geolocati

99838-000
{'geolocation_zip_code_prefix': '99838-000', 'geolocation_city': 'Centenário', 'geolocation_state': 'RS', 'geolocation_street': ''}
99839-000
{'geolocation_zip_code_prefix': '99839-000', 'geolocation_city': '', 'geolocation_state': '', 'geolocation_street': ''}
99840-000
{'geolocation_zip_code_prefix': '99840-000', 'geolocation_city': 'Sananduva', 'geolocation_state': 'RS', 'geolocation_street': ''}
99850-000
{'geolocation_zip_code_prefix': '99850-000', 'geolocation_city': 'Paim Filho', 'geolocation_state': 'RS', 'geolocation_street': ''}
99855-000
{'geolocation_zip_code_prefix': '99855-000', 'geolocation_city': 'São João da Urtiga', 'geolocation_state': 'RS', 'geolocation_street': ''}
99860-000
{'geolocation_zip_code_prefix': '99860-000', 'geolocation_city': 'Cacique Doble', 'geolocation_state': 'RS', 'geolocation_street': ''}
99870-000
{'geolocation_zip_code_prefix': '99870-000', 'geolocation_city': 'São José do Ouro', 'geolocation_state': 'RS', 'geolocation_street': ''}
99

Foi preciso consultar todos os ceps do dataset e salvar no csv

In [52]:
df = spark.createDataFrame(geolocation_formattedCep_address)

/opt/spark/python/pyspark/sql/session.py:346: UserWarning: inferring schema from dict is deprecated,please use pyspark.sql.Row instead
  warnings.warn("inferring schema from dict is deprecated,"


+----------------+-----------------+--------------------+---------------------------+
|geolocation_city|geolocation_state|  geolocation_street|geolocation_zip_code_prefix|
+----------------+-----------------+--------------------+---------------------------+
|       São Paulo|               SP|         Praça da Sé|                  01001-000|
|       São Paulo|               SP|         Rua Direita|                  01002-000|
|       São Paulo|               SP|  Rua José Bonifácio|                  01003-000|
|       São Paulo|               SP|Rua Barão de Para...|                  01004-000|
|       São Paulo|               SP|Rua Benjamim Cons...|                  01005-000|
|       São Paulo|               SP|   Rua Senador Feijó|                  01006-000|
|       São Paulo|               SP|       Rua Riachuelo|                  01007-000|
|       São Paulo|               SP|   Rua Líbero Badaró|                  01008-000|
|       São Paulo|               SP|   Rua Líbero Bada

Neste passo, foi tentado executar o append na base do hive, 
porém, por algum erro as colunas foram trocadas e não consegui resolver

In [58]:
from pyspark.sql import HiveContext

hive_context = HiveContext(spark)
df.write.mode('append').insertInto('olist_cleansed_db.geolocation_tb')

geolocation_tb = hive_context.table("olist_cleansed_db.geolocation_tb")
geolocation_tb.show()

+---------------------------+----------------+--------------------+--------------------+
|geolocation_zip_code_prefix|geolocation_city|   geolocation_state|  geolocation_street|
+---------------------------+----------------+--------------------+--------------------+
|       geolocation_zip_c...|geolocation_city|   geolocation_state|  geolocation_street|
|                   01029901|         Jandira|           São Paulo|Rua Florêncio de ...|
|                   01227200|         Barueri|           São Paulo|            Angélica|
|                   01251000|          Osasco|           São Paulo|  Cardoso de Almeida|
|                   01255010|           Cotia|           São Paulo|            Antonina|
|                   01308040|         Itapevi|           São Paulo|          São Miguel|
|                   01311914|       São Roque|           São Paulo|Avenida Paulista 777|
|                  São Paulo|              SP|         Praça da Sé|           01001-000|
|                  Sã

Transformo dataFrame spark em um dataframe pandas para depois exportar o arquivo csv.

In [63]:
import pandas as pd
result_df = df.select("*").toPandas()

Salvo arquivo em csv

In [72]:
result_df.to_csv("/mnt/notebooks/grupob/olist/geolocation_cep_correios3.csv")

In [1]:
#CSV com o resultado do codigo acima

os.chdir(r'/mnt/notebooks/grupob/olist')

! hadoop fs -put geolocation_cep_correios3.csv /datalake/olist/raw/csv

put: `/datalake/olist/raw/csv/geolocation_cep_correios3.csv': File exists


In [74]:
! hadoop fs -ls /datalake/olist/raw/csv

Found 12 items
-rw-r--r--   2 root supergroup     293133 2022-11-12 21:25 /datalake/olist/raw/csv/geolocation_cep_correios.csv
-rw-r--r--   2 root supergroup     743750 2022-11-18 22:30 /datalake/olist/raw/csv/geolocation_cep_correios2.csv
-rw-r--r--   2 root supergroup     743750 2022-11-19 01:29 /datalake/olist/raw/csv/geolocation_cep_correios3.csv
-rw-r--r--   2 root supergroup    9033957 2022-11-12 16:21 /datalake/olist/raw/csv/olist_customers_dataset.csv
-rw-r--r--   2 root supergroup   61273883 2022-11-12 16:21 /datalake/olist/raw/csv/olist_geolocation_dataset.csv
-rw-r--r--   2 root supergroup   15438671 2022-11-12 16:21 /datalake/olist/raw/csv/olist_order_items_dataset.csv
-rw-r--r--   2 root supergroup    5777138 2022-11-12 16:21 /datalake/olist/raw/csv/olist_order_payments_dataset.csv
-rw-r--r--   2 root supergroup   14451670 2022-11-12 16:21 /datalake/olist/raw/csv/olist_order_reviews_dataset.csv
-rw-r--r--   2 root supergroup   17654914 2022-11-12 16:21 /datalake/olist/raw/

In [75]:
! hdfs dfs -cat /datalake/olist/raw/csv/geolocation_cep_correios3.csv

,geolocation_city,geolocation_state,geolocation_street,geolocation_zip_code_prefix
0,São Paulo,SP,Praça da Sé,01001-000
1,São Paulo,SP,Rua Direita,01002-000
2,São Paulo,SP,Rua José Bonifácio,01003-000
3,São Paulo,SP,Rua Barão de Paranapiacaba,01004-000
4,São Paulo,SP,Rua Benjamim Constant,01005-000
5,São Paulo,SP,Rua Senador Feijó,01006-000
6,São Paulo,SP,Rua Riachuelo,01007-000
7,São Paulo,SP,Rua Líbero Badaró,01008-000
8,São Paulo,SP,Rua Líbero Badaró,01009-000
9,São Paulo,SP,Rua São Bento,01010-000
10,São Paulo,SP,Rua São Bento,01011-000
11,São Paulo,SP,Rua Álvares Penteado,01012-000
12,São Paulo,SP,Rua Quinze de Novembro,01013-000
13,São Paulo,SP,Rua Boa Vista,01014-000
14,São Paulo,SP,Rua General Carneiro,01015-000
15,São Paulo,SP,Rua Venceslau Brás,01016-000
16,São Paulo,SP,Avenida Rangel Pestana,01017-000
17,São Paulo,SP,Praça Clóvis Beviláqua,01018-000
18,São Paulo,SP,Rua Silveira Martins,01019-000
19,São Paulo,SP,Rua Tabatinguera,01020-000
20,São Paulo,SP,Rua Vinte e Cinco de 

713,São Paulo,SP,Rua Cachoeira dos Antunes,02649-000
714,São Paulo,SP,Avenida Mariana Caligiori Ronchetti,02650-000
715,São Paulo,SP,Rua Capitão Ulisses Soares de Campo,02651-000
716,São Paulo,SP,Rua Condessa Amália Matarazzo,02652-000
717,São Paulo,SP,Rua Engenheiro Fritz Leitgeb,02653-000
718,São Paulo,SP,Rua Fernando Pessoa,02670-000
719,São Paulo,SP,Rua Oliveira Martins,02671-000
720,São Paulo,SP,Avenida Masao Watanabe,02672-000
721,São Paulo,SP,Avenida General Penha Brasil,02673-000
722,São Paulo,SP,Rua Ministro Lins de Barros,02674-000
723,São Paulo,SP,Rua Antônio Lopes de Barros,02675-000
724,São Paulo,SP,Rua João Oliveira Salgado,02676-000
725,São Paulo,SP,Rua Taquaraçu de Minas,02677-000
726,São Paulo,SP,Avenida Francisco Machado da Silva,02678-000
727,São Paulo,SP,Rua Alto Sucuriú,02679-000
728,São Paulo,SP,Rua do Itaguacu,02680-000
729,São Paulo,SP,Avenida Otaviano Alves de Lima,02701-000
730,São Paulo,SP,Avenida Professor Celestino Bourroul,02710-000
731,São Paulo,SP,Rua Ma

1689,São Paulo,SP,Rua do Gama,04032-000
1690,São Paulo,SP,Rua Domingos de Morais,04035-000
1691,São Paulo,SP,Rua Domingos de Morais,04036-000
1692,São Paulo,SP,Rua Doutor Diogo de Faria,04037-000
1693,São Paulo,SP,Rua Borges Lagoa,04038-000
1694,São Paulo,SP,Rua Pedro de Toledo,04039-000
1695,São Paulo,SP,Rua Loefgren,04040-000
1696,São Paulo,SP,Avenida Onze de Junho,04041-000
1697,São Paulo,SP,Avenida Doutor Altino Arantes,04042-000
1698,São Paulo,SP,Rua Luís Góis,04043-000
1699,São Paulo,SP,Rua Machado Bitencourt,04044-000
1700,São Paulo,SP,Avenida Jabaquara,04045-000
1701,São Paulo,SP,Avenida Jabaquara,04046-000
1702,São Paulo,SP,Avenida Senador Casimiro da Rocha,04047-000
1703,São Paulo,SP,Rua das Rosas,04048-000
1704,São Paulo,SP,Rua dos Heliotrópios,04049-000
1705,São Paulo,SP,Rua das Orquídeas,04050-000
1706,São Paulo,SP,Rua das Hortênsias,04051-000
1707,São Paulo,SP,Rua Guarau,04052-000
1708,São Paulo,SP,Rua Pero Neto,04053-000
1709,São Paulo,SP,Avenida Afonso Mariano Fagundes,

1915,São Paulo,SP,Rua Doutor Nicolau Alberto Defina,04291-000
1916,São Paulo,SP,Rua Dom Macário,04292-000
1917,São Paulo,SP,Rua do Boqueirão,04293-000
1918,São Paulo,SP,Rua Abagiba,04294-000
1919,São Paulo,SP,Avenida Coronel José Pires de Andrade,04295-000
1920,São Paulo,SP,Avenida Santo Albano,04296-000
1921,São Paulo,SP,Avenida Padre Arlindo Vieira,04297-000
1922,São Paulo,SP,Avenida Deputado Rubens Granja,04298-000
1923,São Paulo,SP,Avenida Miguel Estefno,04301-000
1924,São Paulo,SP,Rua Apotribu,04302-000
1925,São Paulo,SP,Rua Professor Aprígio Gonzaga,04303-000
1926,São Paulo,SP,Avenida Fagundes Filho,04304-000
1927,São Paulo,SP,Rua dos Democratas,04305-000
1928,São Paulo,SP,Avenida Affonso D'Escragnolle Taunay,04306-000
1929,São Paulo,SP,Rua Carlos Villalva,04307-000
1930,São Paulo,SP,Avenida Engenheiro Armando de Arruda Pereira,04308-000
1931,,,,04309-000
1932,São Paulo,SP,Avenida Diederichsen,04310-000
1933,São Paulo,SP,Avenida do Café,04311-000
1934,São Paulo,SP,Rua Barra do Pa

2522,São Paulo,SP,Rua Artur Orlando,05118-000
2523,São Paulo,SP,Avenida do Anastácio,05119-000
2524,São Paulo,SP,Avenida Manoel Domingos Pinto,05120-000
2525,São Paulo,SP,Rua Doutor Odon Carlos de Figueiredo Ferraz,05121-000
2526,São Paulo,SP,Rua Professor Benedito Alarico de Castro Borelli,05122-000
2527,São Paulo,SP,Rua Abraham Lincoln,05123-000
2528,São Paulo,SP,Avenida General Charles de Gaulle,05124-000
2529,São Paulo,SP,Rua Brigadeiro Henrique Fontenelle,05125-000
2530,São Paulo,SP,Rua Homero Sales,05126-000
2531,São Paulo,SP,Rua Armando Martino,05127-000
2532,São Paulo,SP,Rua Willis Roberto Banks,05128-000
2533,São Paulo,SP,Rua José Ataliba Ortiz,05131-000
2534,São Paulo,SP,Rua Rubens de Souza Araújo,05132-000
2535,São Paulo,SP,Rua Joaquim Oliveira Freitas,05133-000
2536,São Paulo,SP,Rua Manoel Martins da Rocha,05134-000
2537,São Paulo,SP,Rua General Lauro Cavalcanti de Farias,05135-000
2538,São Paulo,SP,Avenida Elísio Cordeiro de Siqueira,05136-000
2539,São Paulo,SP,Rua Profess

...

16478,Almirante Tamandaré,PR,Rodovia dos Minérios,83507-000
16479,Almirante Tamandaré,PR,Avenida Fredolin Wolf,83508-000
16480,Almirante Tamandaré,PR,Rua Vereador Wadislau Bugalski,83511-000
16481,Almirante Tamandaré,PR,Rodovia dos Minérios,83512-000
16482,Almirante Tamandaré,PR,Rodovia dos Minérios,83513-000
16483,Almirante Tamandaré,PR,Rodovia dos Minérios,83514-000
16484,Campo Magro,PR,,83535-000
16485,Rio Branco do Sul,PR,,83540-000
16486,Itaperuçu,PR,,83560-000
16487,Cerro Azul,PR,,83570-000
16488,Doutor Ulysses,PR,,83590-000
16489,,,,83600-000
16490,Campo Largo,PR,Rua Centenário,83601-000
16491,Campo Largo,PR,Rua Tenente Waldemar da Silva Miranda,83602-000
16492,Campo Largo,PR,Rodovia PR-423,83603-000
16493,Campo Largo,PR,Rua Leopoldo Okraska,83604-000
16494,,,,83605-000
16495,Campo Largo,PR,Avenida Ademar de Barros,83606-000
16496,Campo Largo,PR,Rodovia BR-277 Curitiba Ponta Grossa,83607-000
16497,Campo Largo,PR,Rodovia BR-277 Curitiba Ponta Grossa,83608-000
16498,Campo Largo,PR

16713,,,,85505-000
16714,,,,85506-000
16715,,,,85507-000
16716,,,,85508-000
16717,Pato Branco,PR,Rua das Garças,85509-000
16718,Pato Branco,PR,,85514-000
16719,Bom Sucesso do Sul,PR,,85515-000
16720,Vitorino,PR,,85520-000
16721,Mariópolis,PR,,85525-000
16722,Clevelândia,PR,,85530-000
16723,Mangueirinha,PR,,85540-000
16724,Honório Serpa,PR,,85548-000
16725,Coronel Vivida,PR,,85550-000
16726,Palmas,PR,,85555-000
16727,Coronel Domingos Soares,PR,,85557-000
16728,Chopinzinho,PR,,85560-000
16729,Sulina,PR,,85565-000
16730,Saudade do Iguaçu,PR,,85568-000
16731,São João,PR,,85570-000
16732,São João,PR,,85571-000
16733,São Jorge D'Oeste,PR,,85575-000
16734,São Jorge D'Oeste,PR,,85579-000
16735,Itapejara d'Oeste,PR,,85580-000
16736,Verê,PR,,85585-000
16737,Cruzeiro do Iguaçu,PR,,85598-000
16738,Francisco Beltrão,PR,Avenida Júlio Assis Cavalheiro,85601-000
16739,Francisco Beltrão,PR,Rua Santo Antônio,85602-000
16740,Francisco Beltrão,PR,Avenida Antônio Sílvio Barbieri,85603-000
16741,Francisco B

17285,Florianópolis,SC,Rua dos Crisântemos,88053-000
17286,Florianópolis,SC,Rua Madre Maria Vilac,88054-000
17287,Florianópolis,SC,Avenida Luiz Boiteux Piazza,88056-000
17288,Florianópolis,SC,Rodovia Armando Calil Bulos,88058-000
17289,Florianópolis,SC,Rodovia João Gualberto Soares,88060-000
17290,Florianópolis,SC,Servidão Timóteo José Mariano,88061-000
17291,Florianópolis,SC,Avenida Afonso Delambert Neto,88062-000
17292,Florianópolis,SC,Avenida Pequeno Príncipe,88063-000
17293,Florianópolis,SC,Rodovia Baldicero Filomeno,88064-000
17294,Florianópolis,SC,Rodovia Francisco Magno Vieira,88065-000
17295,Florianópolis,SC,Rodovia Francisco Thomaz dos Santos,88066-000
17296,Florianópolis,SC,Rodovia Francisco Thomaz dos Santos,88067-000
17297,Florianópolis,SC,Rua General Eurico Gaspar Dutra,88070-000
17298,Florianópolis,SC,Rua Fúlvio Aducci,88075-000
17299,Florianópolis,SC,Avenida Engenheiro Max de Souza,88080-000
17300,Florianópolis,SC,Avenida Governador Ivo Silveira,88085-000
17301,Florianóp

18157,Sapiranga,RS,Avenida Vinte de Setembro,93819-000
18158,Sapiranga,RS,Avenida Maria de Oliveira,93820-000
18159,Sapiranga,RS,Avenida Vinte de Setembro,93821-000
18160,Sapiranga,RS,Avenida Vinte de Setembro,93822-000
18161,Araricá,RS,,93880-000
18162,Nova Hartz,RS,,93890-000
18163,Ivoti,RS,,93900-000
18164,Lindolfo Collor,RS,,93940-000
18165,Presidente Lucena,RS,,93945-000
18166,Dois Irmãos,RS,,93950-000
18167,Morro Reuter,RS,,93990-000
18168,Santa Maria do Herval,RS,,93995-000
18169,Gravataí,RS,Avenida José Loureiro da Silva,94010-000
18170,Gravataí,RS,Rua Boa Vista,94015-000
18171,Gravataí,RS,Avenida General Osório,94020-000
18172,Gravataí,RS,Rua Ibirapuita,94025-000
18173,Gravataí,RS,Avenida Dorival Cândido Luz de Oliveira,94030-000
18174,Gravataí,RS,Rua Paulino C. de Souza,94035-000
18175,Gravataí,RS,Avenida Dorival Cândido Luz de Oliveira,94040-000
18176,Gravataí,RS,Rua Rio Grande do Sul,94045-000
18177,Gravataí,RS,Avenida Dorival Cândido Luz de Oliveira,94050-000
18178,Gravata

18501,Pelotas,RS,Avenida Duque de Caxias,96030-000
18502,Pelotas,RS,Avenida Presidente João Belchior Marques Goulart,96040-000
18503,Pelotas,RS,Rua Major Francisco Nunes de Souza,96045-000
18504,Pelotas,RS,Rua Professor Paulo Zanotta da Cruz,96050-000
18505,,,,96055-000
18506,Pelotas,RS,Avenida Cristóvão José dos Santos,96060-000
18507,,,,96065-000
18508,,,,96070-000
18509,,,,96071-000
18510,,,,96072-000
18511,Pelotas,RS,Avenida Bento Gonçalves,96075-000
18512,,,,96076-000
18513,Pelotas,RS,Rua Visconde de Ouro Preto,96077-000
18514,,,,96080-000
18515,,,,96081-000
18516,,,,96083-000
18517,Pelotas,RS,Avenida Ferreira Viana,96085-000
18518,Pelotas,RS,Rua Attilio Michelon,96087-000
18519,,,,96090-000
18520,,,,96095-000
18521,,,,96100-000
18522,Pelotas,RS,,96115-000
18523,Pelotas,RS,,96130-000
18524,Pelotas,RS,,96145-000
18525,Turuçu,RS,,96148-000
18526,Morro Redondo,RS,,96150-000
18527,Arroio do Padre,RS,,96155-000
18528,Capão do Leão,RS,,96160-000
18529,São Lourenço do Sul,RS,,96170-000
1

Removo os arquivos testes gerado anteriormente e faço o backup do resultado da consulta do pycep

In [11]:
! hdfs dfs -rm /datalake/olist/raw/csv/geolocation_cep_correios.csv

Deleted /datalake/olist/raw/csv/geolocation_cep_correios.csv


In [4]:
! hdfs dfs -mkdir /datalake/olist/raw/csv/bkp
! hdfs dfs -cp /datalake/olist/raw/csv/geolocation_cep_correios3.csv /datalake/olist/raw/csv/bkp
! hadoop fs -ls /datalake/olist/raw/csv/bkp

Found 1 items
-rw-r--r--   2 root supergroup     743750 2022-11-19 19:23 /datalake/olist/raw/csv/bkp/geolocation_cep_correios3.csv


In [6]:
! hadoop fs -mv /datalake/olist/raw/csv/geolocation_cep_correios3.csv /datalake/olist/raw/csv/geolocation_cep_correios.csv
! hadoop fs -ls /datalake/olist/raw/csv/

Found 12 items
drwxr-xr-x   - root supergroup          0 2022-11-19 19:23 /datalake/olist/raw/csv/bkp
-rw-r--r--   2 root supergroup     743750 2022-11-19 01:29 /datalake/olist/raw/csv/geolocation_cep_correios.csv
-rw-r--r--   2 root supergroup     743750 2022-11-18 22:30 /datalake/olist/raw/csv/geolocation_cep_correios2.csv
-rw-r--r--   2 root supergroup    9033957 2022-11-12 16:21 /datalake/olist/raw/csv/olist_customers_dataset.csv
-rw-r--r--   2 root supergroup   61273883 2022-11-12 16:21 /datalake/olist/raw/csv/olist_geolocation_dataset.csv
-rw-r--r--   2 root supergroup   15438671 2022-11-12 16:21 /datalake/olist/raw/csv/olist_order_items_dataset.csv
-rw-r--r--   2 root supergroup    5777138 2022-11-12 16:21 /datalake/olist/raw/csv/olist_order_payments_dataset.csv
-rw-r--r--   2 root supergroup   14451670 2022-11-12 16:21 /datalake/olist/raw/csv/olist_order_reviews_dataset.csv
-rw-r--r--   2 root supergroup   17654914 2022-11-12 16:21 /datalake/olist/raw/csv/olist_orders_dataset.c

In [15]:
#caso der erro recupero o backup
#! hdfs dfs -cp /datalake/olist/raw/csv/bkp/geolocation_cep_correios3.csv /datalake/olist/raw/csv/
#! hadoop fs -mv /datalake/olist/raw/csv/geolocation_cep_correios3.csv /datalake/olist/raw/csv/geolocation_cep_correios.csv
#! hadoop fs -ls /datalake/olist/raw/csv/

Found 12 items
drwxr-xr-x   - root supergroup          0 2022-11-19 19:23 /datalake/olist/raw/csv/bkp
-rw-r--r--   2 root supergroup     743750 2022-11-19 20:40 /datalake/olist/raw/csv/geolocation_cep_correios.csv
-rw-r--r--   2 root supergroup     743750 2022-11-18 22:30 /datalake/olist/raw/csv/geolocation_cep_correios2.csv
-rw-r--r--   2 root supergroup    9033957 2022-11-12 16:21 /datalake/olist/raw/csv/olist_customers_dataset.csv
-rw-r--r--   2 root supergroup   61273883 2022-11-12 16:21 /datalake/olist/raw/csv/olist_geolocation_dataset.csv
-rw-r--r--   2 root supergroup   15438671 2022-11-12 16:21 /datalake/olist/raw/csv/olist_order_items_dataset.csv
-rw-r--r--   2 root supergroup    5777138 2022-11-12 16:21 /datalake/olist/raw/csv/olist_order_payments_dataset.csv
-rw-r--r--   2 root supergroup   14451670 2022-11-12 16:21 /datalake/olist/raw/csv/olist_order_reviews_dataset.csv
-rw-r--r--   2 root supergroup   17654914 2022-11-12 16:21 /datalake/olist/raw/csv/olist_orders_dataset.c

Precisei remover a coluna Index do CSV, por isso refiz o arquivo

In [7]:
import pandas as pd
csv2 =pd.read_csv("/mnt/notebooks/grupob/olist/geolocation_cep_correios.csv")
csv2.to_csv("/mnt/notebooks/grupob/olist/geolocation_cep_correios.csv",index=False)


In [8]:

os.chdir(r'/mnt/notebooks/grupob/olist')

! hadoop fs -put geolocation_cep_correios.csv /datalake/olist/raw/csv

In [12]:
! hadoop fs -ls /datalake/olist/raw/csv
! hdfs dfs -cat /datalake/olist/raw/csv/geolocation_cep_correios.csv

Found 12 items
drwxr-xr-x   - root supergroup          0 2022-11-19 19:23 /datalake/olist/raw/csv/bkp
-rw-r--r--   3 root supergroup     640769 2022-11-19 22:08 /datalake/olist/raw/csv/geolocation_cep_correios.csv
-rw-r--r--   2 root supergroup     743750 2022-11-18 22:30 /datalake/olist/raw/csv/geolocation_cep_correios2.csv
-rw-r--r--   2 root supergroup    9033957 2022-11-12 16:21 /datalake/olist/raw/csv/olist_customers_dataset.csv
-rw-r--r--   2 root supergroup   61273883 2022-11-12 16:21 /datalake/olist/raw/csv/olist_geolocation_dataset.csv
-rw-r--r--   2 root supergroup   15438671 2022-11-12 16:21 /datalake/olist/raw/csv/olist_order_items_dataset.csv
-rw-r--r--   2 root supergroup    5777138 2022-11-12 16:21 /datalake/olist/raw/csv/olist_order_payments_dataset.csv
-rw-r--r--   2 root supergroup   14451670 2022-11-12 16:21 /datalake/olist/raw/csv/olist_order_reviews_dataset.csv
-rw-r--r--   2 root supergroup   17654914 2022-11-12 16:21 /datalake/olist/raw/csv/olist_orders_dataset.c

São Paulo,SP,Rua Cruz de Malta,02248-000
São Paulo,SP,Rua Cândido Figueiredo,02249-000
São Paulo,SP,Rua Rio Doce,02250-000
São Paulo,SP,Rua Tanque Velho,02251-000
São Paulo,SP,Rua Mata Redonda,02252-000
São Paulo,SP,Rua Dragões da Independência,02253-000
São Paulo,SP,Rua Capricho,02254-000
São Paulo,SP,Rua Rabelo da Cruz,02255-000
São Paulo,SP,Rua das Vertentes,02256-000
São Paulo,SP,Rua Doutor Nicolino Morena,02257-000
São Paulo,SP,Avenida Júlio Buono,02258-000
São Paulo,SP,Avenida Francisco Rodrigues,02259-000
São Paulo,SP,Avenida Luís Stamatis,02260-000
São Paulo,SP,Rua Parazinho,02261-000
São Paulo,SP,Rua Guajarás,02262-000
São Paulo,SP,Rua Irmã Filomena,02263-000
São Paulo,SP,Rua Igarité,02264-000
São Paulo,SP,Avenida Guapira,02265-000
São Paulo,SP,Avenida Maestro Villa-Lobos,02266-000
São Paulo,SP,Rua Paulo de Faria,02267-000
São Paulo,SP,Rua Pero Vidal,02268-000
São Paulo,SP,Avenida Comandante Antônio Paiva Sampaio,02269-000
São Paulo,SP,Rua Murilo Furtado,02270-000
São Paulo,SP

São Paulo,SP,Rua Friedrich Von Voith,02995-000
São Paulo,SP,Rua Antônio de Cabezon,02996-000
São Paulo,SP,Travessa Antônio Inácio Torres,02997-000
São Paulo,SP,Avenida Nelson Palma Travassos,02998-000
São Paulo,SP,Avenida Rangel Pestana,03001-000
São Paulo,SP,Avenida Rangel Pestana,03002-000
São Paulo,SP,Rua da Figueira,03003-000
São Paulo,SP,Rua do Gasômetro,03004-000
São Paulo,SP,Rua do Lucas,03005-000
,,,03006-000
São Paulo,SP,Avenida Mercúrio,03007-000
São Paulo,SP,Rua Monsenhor Andrade,03008-000
São Paulo,SP,Rua João Teodoro,03009-000
São Paulo,SP,Rua Barão de Ladário,03010-000
São Paulo,SP,Rua Maria Marcolina,03011-000
São Paulo,SP,Rua Conselheiro Belisário,03012-000
São Paulo,SP,Rua Casimiro de Abreu,03013-000
São Paulo,SP,Avenida Celso Garcia,03014-000
São Paulo,SP,Avenida Celso Garcia,03015-000
São Paulo,SP,Rua Oriente,03016-000
São Paulo,SP,Rua Bresser,03017-000
São Paulo,SP,Rua João Boemer,03018-000
São Paulo,SP,Rua Joaquim Carlos,03019-000
São Paulo,SP,Rua Marcos Arruda,030

São Paulo,SP,Avenida Israel Fonseca,03920-000
São Paulo,SP,Rua Pedro de Castro Velho,03921-000
São Paulo,SP,Rua Benedito Jacinto Mendes,03922-000
São Paulo,SP,Rua Dionísio Aguado Garcia,03923-000
São Paulo,SP,Rua Alexandre Fernandes,03924-000
São Paulo,SP,Rua Leandro de Sevilha,03925-000
São Paulo,SP,Rua Dom Gregório dos Anjos,03926-000
São Paulo,SP,Rua Rio das Flores,03927-000
São Paulo,SP,Rua José Ferrer,03928-000
São Paulo,SP,Rua Lúcio Cardim Filho,03929-000
São Paulo,SP,Rua Arão Reis,03930-000
São Paulo,SP,Rua Felisberto Augusto de Oliveira,03931-000
São Paulo,SP,Rua Santana do Riacho,03932-000
São Paulo,SP,Rua Poços de Caldas,03933-000
São Paulo,SP,Rua São João do Paraíso,03934-000
São Paulo,SP,Rua Estado do Amazonas,03935-000
São Paulo,SP,Rua Estado do Ceará,03936-000
São Paulo,SP,Rua Sargento Noel de Camargo,03937-000
São Paulo,SP,Rua Urucuia,03938-000
São Paulo,SP,Rua Caiana,03939-000
São Paulo,SP,Rua Campo Florido,03940-000
São Paulo,SP,Rua Capetinga,03941-000
São Paulo,SP,Ave

São Paulo,SP,Rua dos Caciques,04145-000
São Paulo,SP,Rua Artur Thiré,04146-000
São Paulo,SP,Rua Auguste Clesinger,04147-000
São Paulo,SP,Rua Francisco Dias,04148-000
São Paulo,SP,Rua Quisisana,04149-000
São Paulo,SP,Rua Ribeiro Lacerda,04150-000
São Paulo,SP,Rua Frei Rolim,04151-000
São Paulo,SP,Rua Elisa Silveira,04152-000
São Paulo,SP,Rua Francisco Tapajós,04153-000
São Paulo,SP,Rua Coronel Silvério Magalhães,04154-000
São Paulo,SP,Rua Rosa de Morais,04155-000
São Paulo,SP,Rua Vicente Fernandes Pinto,04156-000
São Paulo,SP,Rua Eduardo Ferreira Franca,04157-000
São Paulo,SP,Rua Divinópolis,04158-000
São Paulo,SP,Rua Nossa Senhora da Saúde,04159-000
São Paulo,SP,Rua Dom Vilares,04160-000
São Paulo,SP,Rua dos Operários,04161-000
São Paulo,SP,Rua Marquês de Lages,04162-000
São Paulo,SP,Rua Evolução,04163-000
São Paulo,SP,Rua Romão Puiggari,04164-000
São Paulo,SP,Rua Nossa Senhora das Mercês,04165-000
São Paulo,SP,Avenida Padre Arlindo Vieira,04166-000
São Paulo,SP,Rua Simão Lopes,04167-0

...

,,,57310-000
,,,57311-000
,,,57312-000
Arapiraca,AL,Rua Santa Rita,57313-000
,,,57314-000
,,,57315-000
,,,57316-000
Arapiraca,AL,Rodovia AL-220,57317-000
,,,57319-000
Craíbas,AL,,57320-000
Coité do Nóia,AL,,57325-000
Lagoa da Canoa,AL,,57330-000
Feira Grande,AL,,57340-000
Campo Grande,AL,,57350-000
Girau do Ponciano,AL,,57360-000
Traipu,AL,,57370-000
São Brás,AL,,57380-000
Olho D'Água Grande,AL,,57390-000
Pão de Açúcar,AL,,57400-000
Palestina,AL,,57410-000
Batalha,AL,,57420-000
Jaramataia,AL,,57425-000
Jacaré dos Homens,AL,,57430-000
Monteirópolis,AL,,57440-000
Olho D'Água das Flores,AL,,57442-000
São José da Tapera,AL,,57445-000
Piranhas,AL,,57460-000
Olho D'Água do Casado,AL,,57470-000
Pariconha,AL,,57475-000
Delmiro Gouveia,AL,,57480-000
Água Branca,AL,,57490-000
Santana do Ipanema,AL,,57500-000
Poço das Trincheiras,AL,,57510-000
Senador Rui Palmeira,AL,,57515-000
Maravilha,AL,,57520-000
Ouro Branco,AL,,57525-000
Canapi,AL,,57530-000
Carneiros,AL,,57535-000
Mata Grande,AL,,57540-000

Sousa,PB,Rua Manoel Gadelha Filho,58802-000
,,,58804-000
Sousa,PB,Rua Assis Chateaubriand,58805-000
Sousa,PB,Avenida Saul Pedrosa de Sá Melo,58806-000
,,,58807-000
Sousa,PB,Rua Salustiano José Pinto,58808-000
São José da Lagoa Tapada,PB,,58815-000
Nazarezinho,PB,,58817-000
São Francisco,PB,,58818-000
Marizópolis,PB,,58819-000
Lastro,PB,,58820-000
Aparecida,PB,,58823-000
Santa Cruz,PB,,58824-000
Jericó,PB,,58830-000
Mato Grosso,PB,,58832-000
Lagoa,PB,,58835-000
Pombal,PB,,58840-000
São Bentinho,PB,,58857-000
Paulista,PB,,58860-000
São Bento,PB,,58865-000
Riacho dos Cavalos,PB,,58870-000
Brejo dos Santos,PB,,58880-000
Catolé do Rocha,PB,,58884-000
Bom Sucesso,PB,,58887-000
Brejo do Cruz,PB,,58890-000
São José do Brejo do Cruz,PB,,58893-000
Belém do Brejo do Cruz,PB,,58895-000
Cajazeiras,PB,,58900-000
Poço de José de Moura,PB,,58908-000
São João do Rio do Peixe,PB,,58910-000
Uiraúna,PB,,58915-000
Triunfo,PB,,58920-000
Bernardino Batista,PB,,58922-000
Santa Helena,PB,,58925-000
Joca Claudi

Brasília,DF,SQN 207,70852-000
Brasília,DF,SQN 208,70853-000
Brasília,DF,SQN 209,70854-000
Brasília,DF,SQN 407,70855-000
Brasília,DF,SQN 408,70856-000
Brasília,DF,SQN 409,70857-000
Brasília,DF,SQN 210,70862-000
Brasília,DF,SQN 211,70863-000
Brasília,DF,SQN 212,70864-000
Brasília,DF,SQN 410,70865-000
Brasília,DF,SQN 411,70866-000
Brasília,DF,SQN 412,70867-000
Brasília,DF,SQN 213,70872-000
Brasília,DF,SQN 214,70873-000
Brasília,DF,SQN 215,70874-000
Brasília,DF,SQN 216,70875-000
Brasília,DF,SQN 413,70876-000
Brasília,DF,SQN 415,70878-000
Brasília,DF,SQN 416,70879-000
,,,70908-000
Brasília,DF,Campus Universitário Darcy Ribeiro,70910-000
Brasília,DF,SQB 1,71009-000
,,,71010-000
,,,71015-000
,,,71020-000
,,,71050-000
Brasília,DF,QE 28,71060-000
,,,71065-000
,,,71070-000
,,,71090-000
Brasília,DF,EPTG QE 1,71100-000
Brasília,DF,SPMS II,71200-000
,,,71205-000
Brasília,DF,SIA Setor de Áreas Públicas,71215-000
,,,71218-000
Brasília,DF,SIN,71225-000
Brasília,DF,SCIA Quadra 15,71250-000
,,,71503-000

Ponta Grossa,PR,Rua Teixeira Mendes,84031-000
Ponta Grossa,PR,Avenida Euzébio de Queiroz,84032-000
Ponta Grossa,PR,Rua Siqueira Campos,84033-000
Ponta Grossa,PR,Rua Ermelino de Leão,84035-000
Ponta Grossa,PR,Rua Dom Pedro I,84036-000
Ponta Grossa,PR,Rua Arapoti,84037-000
Ponta Grossa,PR,Rua Balduíno Taques,84040-000
Ponta Grossa,PR,Avenida Visconde de Mauá,84043-000
Ponta Grossa,PR,Estrada Eugênio Ricetti,84045-000
,,,84046-000
Ponta Grossa,PR,Rua Joaquim de Paula Xavier,84050-000
Ponta Grossa,PR,Avenida Visconde de Taunay,84051-000
Ponta Grossa,PR,Avenida Visconde de Taunay,84052-000
Ponta Grossa,PR,Avenida Dom Pedro II,84053-000
,,,84060-000
Ponta Grossa,PR,Rua Nicolau Kluppel Neto,84061-000
Ponta Grossa,PR,Avenida Souza Naves,84062-000
Ponta Grossa,PR,Avenida Souza Naves,84063-000
Ponta Grossa,PR,Avenida Souza Naves,84064-000
Ponta Grossa,PR,Rua do Advogado,84065-000
Ponta Grossa,PR,Avenida Ernesto Vilela,84070-000
Ponta Grossa,PR,Rua Centenário do Sul,84071-000
Ponta Grossa,PR,Rua 

Porto Alegre,RS,Rua Voluntários da Pátria,90030-000
Porto Alegre,RS,Rua Ramiro Barcelos,90035-000
,,,90038-000
Porto Alegre,RS,Avenida João Pessoa,90040-000
Porto Alegre,RS,Rua José do Patrocínio,90050-000
Porto Alegre,RS,Avenida Presidente Vargas,90090-000
Porto Alegre,RS,Avenida Praia de Belas,90110-000
,,,90119-000
,,,90120-000
Porto Alegre,RS,Rua Marcílio Dias,90130-000
Porto Alegre,RS,Avenida Getúlio Vargas,90150-000
Porto Alegre,RS,Avenida da Azenha,90160-000
,,,90169-000
,,,90170-000
Porto Alegre,RS,Avenida dos Estados,90200-000
Porto Alegre,RS,Avenida Farrapos,90220-000
Porto Alegre,RS,Avenida Presidente Franklin Roosevelt,90230-000
,,,90231-000
Porto Alegre,RS,Avenida Pernambuco,90240-000
,,,90241-000
Porto Alegre,RS,Avenida A. J. Renner,90245-000
Porto Alegre,RS,Avenida A. J. Renner,90250-000
,,,90251-000
Porto Alegre,RS,Avenida Protásio Alves,90410-000
Porto Alegre,RS,Rua Casemiro de Abreu,90420-000
Porto Alegre,RS,Rua Mostardeiro,90430-000
Porto Alegre,RS,Rua Coronel Bordin

In [5]:
schema = StructType() \
      .add("geolocation_city",StringType(),True) \
      .add("geolocation_state",StringType(),True) \
      .add("geolocation_street",StringType(),True) \
      .add("geo_zip_code_prefix",StringType(),True) 


geolocation_correios_df = spark.read.option("header",True) \
                       .option("delimiter",",") \
                       .schema(schema) \
                       .csv("hdfs://namenode:8020/datalake/olist/raw/csv/geolocation_cep_correios.csv")

In [7]:
geolocation_correios_df.show()

+----------------+-----------------+--------------------+-------------------+
|geolocation_city|geolocation_state|  geolocation_street|geo_zip_code_prefix|
+----------------+-----------------+--------------------+-------------------+
|       São Paulo|               SP|         Praça da Sé|          01001-000|
|       São Paulo|               SP|         Rua Direita|          01002-000|
|       São Paulo|               SP|  Rua José Bonifácio|          01003-000|
|       São Paulo|               SP|Rua Barão de Para...|          01004-000|
|       São Paulo|               SP|Rua Benjamim Cons...|          01005-000|
|       São Paulo|               SP|   Rua Senador Feijó|          01006-000|
|       São Paulo|               SP|       Rua Riachuelo|          01007-000|
|       São Paulo|               SP|   Rua Líbero Badaró|          01008-000|
|       São Paulo|               SP|   Rua Líbero Badaró|          01009-000|
|       São Paulo|               SP|       Rua São Bento|       

In [24]:
from pyspark.sql import HiveContext

hive_context = HiveContext(spark)
#geolocation_correios_df.write.mode('append').insertInto('olist_cleansed_db.geolocation_tb')

geolocation_tb = hive_context.table("olist_cleansed_db.geolocation_tb")
geolocation_tb.show()

+----------------+-----------------+--------------------+---------------------------+
|geolocation_city|geolocation_state|  geolocation_street|geolocation_zip_code_prefix|
+----------------+-----------------+--------------------+---------------------------+
|geolocation_city|geolocation_state|  geolocation_street|       geolocation_zip_c...|
|       São Paulo|               SP|         Praça da Sé|                  01001-000|
|       São Paulo|               SP|         Rua Direita|                  01002-000|
|       São Paulo|               SP|  Rua José Bonifácio|                  01003-000|
|       São Paulo|               SP|Rua Barão de Para...|                  01004-000|
|       São Paulo|               SP|Rua Benjamim Cons...|                  01005-000|
|       São Paulo|               SP|   Rua Senador Feijó|                  01006-000|
|       São Paulo|               SP|       Rua Riachuelo|                  01007-000|
|       São Paulo|               SP|   Rua Líbero Bada

In [26]:
df=spark.sql("show databases")
df.show()

+--------------------+
|        databaseName|
+--------------------+
|             default|
|             estudos|
|   olist_cleansed_db|
|olist_consumption_db|
|   olist_enriched_db|
|    olist_trusted_db|
+--------------------+



In [27]:
df1=spark.sql("select * from olist_cleansed_db.geolocation_tb")
df1.show()

+----------------+-----------------+--------------------+---------------------------+
|geolocation_city|geolocation_state|  geolocation_street|geolocation_zip_code_prefix|
+----------------+-----------------+--------------------+---------------------------+
|geolocation_city|geolocation_state|  geolocation_street|       geolocation_zip_c...|
|       São Paulo|               SP|         Praça da Sé|                  01001-000|
|       São Paulo|               SP|         Rua Direita|                  01002-000|
|       São Paulo|               SP|  Rua José Bonifácio|                  01003-000|
|       São Paulo|               SP|Rua Barão de Para...|                  01004-000|
|       São Paulo|               SP|Rua Benjamim Cons...|                  01005-000|
|       São Paulo|               SP|   Rua Senador Feijó|                  01006-000|
|       São Paulo|               SP|       Rua Riachuelo|                  01007-000|
|       São Paulo|               SP|   Rua Líbero Bada

In [6]:
geoclocation_cep_distinct_df.join(geolocation_df,geolocation_df.geolocation_zip_code_prefix == geoclocation_cep_distinct_df.geolocation_zip_code_prefix, "inner")\
.drop(geoclocation_cep_distinct_df["geolocation_zip_code_prefix"])\
.count()

1000163

In [7]:
geoclocation_cep_distinct_df.count()

19015

In [11]:
! pip install geopy

In [8]:
import time
from geopy.geocoders import Nominatim

#adding new row with address provided by geopy
def getCepByLatLon(row):    
    rowDict = row.asDict()
    
    
    city = rowDict.get("geolocation_city")
    street = rowDict.get("geolocation_state")
    print(city)
    print(street)
    
    if(street!= "" and street!="-1" and street!="-2"):
        address = "{street} {city}"
        geolocator = Nominatim(user_agent="update_geolocation")
        location = geolocator.geocode(address.format(street=street,city=city))
        print(location.latitude)
        rowDict["geolocation_lat"] = str(location.latitude)
        rowDict["geolocation_lon"] = str(location.longitude)
    time.sleep(4)
    return rowDict


In [9]:
geolocation_valid_df = geolocation_correios_df.select("*").where(col("geo_zip_code_prefix")!="geolocation_zip_code_prefix")

In [10]:
geolocation_valid_df.cache()

DataFrame[geolocation_city: string, geolocation_state: string, geolocation_street: string, geo_zip_code_prefix: string]

In [14]:
geolocation_valid_df.count()

19015

In [11]:
geolocation_valid_df = geolocation_valid_df.select("*").where(col("geolocation_street").isNotNull())

geolocation_valid_df.show()

+----------------+-----------------+--------------------+-------------------+
|geolocation_city|geolocation_state|  geolocation_street|geo_zip_code_prefix|
+----------------+-----------------+--------------------+-------------------+
|       São Paulo|               SP|         Praça da Sé|          01001-000|
|       São Paulo|               SP|         Rua Direita|          01002-000|
|       São Paulo|               SP|  Rua José Bonifácio|          01003-000|
|       São Paulo|               SP|Rua Barão de Para...|          01004-000|
|       São Paulo|               SP|Rua Benjamim Cons...|          01005-000|
|       São Paulo|               SP|   Rua Senador Feijó|          01006-000|
|       São Paulo|               SP|       Rua Riachuelo|          01007-000|
|       São Paulo|               SP|   Rua Líbero Badaró|          01008-000|
|       São Paulo|               SP|   Rua Líbero Badaró|          01009-000|
|       São Paulo|               SP|       Rua São Bento|       

In [15]:
geolocation_valid_rows = geolocation_valid_df.collect()

Crio um dataframe spark vazio para armazenar os ceps temporarios da consulta

In [31]:
from pyspark.sql.types import StructType,StructField, StringType
schema = StructType([StructField("geo_zip_code_prefix",StringType(),True)])

table_temp = spark.createDataFrame([["00000-000"]],schema=schema)
#df_temp = geolocation_valid_df.select("geo_zip_code_prefix").limit(20)
table_temp.show()

+-------------------+
|geo_zip_code_prefix|
+-------------------+
|          00000-000|
+-------------------+



In [40]:
table_temp.createOrReplaceTempView("table_temp")
geolocation_valid_df.createOrReplaceTempView("geolocation_valid_df")
df_select = spark.sql("""select geo_zip_code_prefix from geolocation_valid_df  where not exists (select 1 from table_temp where geolocation_valid_df.geo_zip_code_prefix = table_temp.geo_zip_code_prefix) limit 10 """)
df_select.write.mode("overwrite").insertInto("table_temp")


AnalysisException: "unresolved operator 'InsertIntoTable LogicalRDD [geo_zip_code_prefix#450], false, false, false;;\n'InsertIntoTable LogicalRDD [geo_zip_code_prefix#450], false, false, false\n+- GlobalLimit 10\n   +- LocalLimit 10\n      +- Project [geo_zip_code_prefix#95]\n         +- Filter NOT exists#479 [geo_zip_code_prefix#95]\n            :  +- Project [1 AS 1#480]\n            :     +- Filter (outer(geo_zip_code_prefix#95) = geo_zip_code_prefix#450)\n            :        +- SubqueryAlias `table_temp`\n            :           +- LogicalRDD [geo_zip_code_prefix#450], false\n            +- SubqueryAlias `geolocation_valid_df`\n               +- Filter isnotnull(geolocation_street#94)\n                  +- Project [geolocation_city#92, geolocation_state#93, geolocation_street#94, geo_zip_code_prefix#95]\n                     +- Filter NOT (geo_zip_code_prefix#95 = geolocation_zip_code_prefix)\n                        +- Project [geolocation_city#92, geolocation_state#93, geolocati

In [20]:
df_select = spark.sql("""select geo_zip_code_prefix from geolocation_valid_df  where not exists (select 1 from table_temp where geolocation_valid_df.geo_zip_code_prefix = table_temp.geo_zip_code_prefix) limit 10 """)


+-------------------+
|geo_zip_code_prefix|
+-------------------+
|          02020-000|
|          02132-000|
|          02205-000|
|          02250-000|
|          02735-000|
|          03077-000|
|          03152-000|
|          03377-000|
|          03523-000|
|          03950-000|
+-------------------+



In [26]:
spark.sql("""select * from table_temp""")

DataFrame[geo_zip_code_prefix: string]

In [28]:
df_select.write.mode("append").insertInto("table_temp")

AnalysisException: "unresolved operator 'InsertIntoTable LogicalRDD [geo_zip_code_prefix#250], false, false, false;;\n'InsertIntoTable LogicalRDD [geo_zip_code_prefix#250], false, false, false\n+- GlobalLimit 10\n   +- LocalLimit 10\n      +- Project [geo_zip_code_prefix#95]\n         +- Filter NOT exists#347 [geo_zip_code_prefix#95]\n            :  +- Project [1 AS 1#348]\n            :     +- Filter (outer(geo_zip_code_prefix#95) = geo_zip_code_prefix#250)\n            :        +- SubqueryAlias `table_temp`\n            :           +- LogicalRDD [geo_zip_code_prefix#250], false\n            +- SubqueryAlias `geolocation_valid_df`\n               +- Filter isnotnull(geolocation_street#94)\n                  +- Project [geolocation_city#92, geolocation_state#93, geolocation_street#94, geo_zip_code_prefix#95]\n                     +- Filter NOT (geo_zip_code_prefix#95 = geolocation_zip_code_prefix)\n                        +- Project [geolocation_city#92, geolocation_state#93, geolocati

In [33]:
geolocation_latlon_address = [
        getCepByLatLon(row)
        for row in geolocation_valid_rows
     ]

São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507
São Paulo
SP
-23.5506507


KeyboardInterrupt: 

OBS: O código funcionou, porém, por algum motivo que não identifiquei a conexão com a geoPy esta falhando.

In [15]:
geolocation_latlon_address_df = spark.createDataFrame(geolocation_latlon_address)
geolocation_latlon_address_df.show()

NameError: name 'geolocation_latlon_address_df' is not defined